# 한국투자증권 API연결 함수

In [1]:
import requests
import json
import datetime
import time
import yaml


# config.yaml 파일 읽기
with open('config.yaml', encoding='UTF-8') as f:	    # config.yaml 파일을 f로 사용
    _cfg = yaml.load(f, Loader=yaml.FullLoader)
APP_KEY = _cfg['APP_KEY']               # 앱키
APP_SECRET = _cfg['APP_SECRET']         # 앱시크릿
ACCESS_TOKEN = ""                       # 토큰은 25번 라인
CANO = _cfg['CANO']                     # 계좌 앞 8자리
ACNT_PRDT_CD = _cfg['ACNT_PRDT_CD']     # 계좌 뒤 2자리
DISCORD_WEBHOOK_URL = _cfg['DISCORD_WEBHOOK_URL']   # 디스코드 URL
URL_BASE = _cfg['URL_BASE']             # 실전투자 or 모의투자

# 디스코드 메시지 전송
def send_message(msg):
    """디스코드 메세지 전송"""
    now = datetime.datetime.now()
    message = {"content": f"[{now.strftime('%Y-%m-%d %H:%M:%S')}] {str(msg)}"}
    requests.post(DISCORD_WEBHOOK_URL, data=message)
    print(message)


# 토큰 발급
def get_access_token():                                 # POST 방식
    headers = {"content-type":"application/json"}       # 기본정보(Content-Type)
    body = {"grant_type":"client_credentials",          # R : 권한부여 타입
    "appkey":APP_KEY,                                   # R 
    "appsecret":APP_SECRET}                             # R 
    PATH = "oauth2/tokenP"                              # 기본정보(URL) : URL
    URL = f"{URL_BASE}/{PATH}"                          # 기본정보(도메인) : https://openapivts.koreainvestment.com:29443/oauth2/tokenP
    res = requests.post(URL, headers=headers, data=json.dumps(body))	# Response 데이터 호출
    ACCESS_TOKEN = res.json()["access_token"]
    return ACCESS_TOKEN


def hashkey(datas):
    """암호화"""
    PATH = "uapi/hashkey"
    URL = f"{URL_BASE}/{PATH}"
    headers = {
    'content-Type' : 'application/json',
    'appKey' : APP_KEY,
    'appSecret' : APP_SECRET,
    }
    res = requests.post(URL, headers=headers, data=json.dumps(datas))
    hashkey = res.json()["HASH"]
    return hashkey


# 주식 현재가 시세
def get_current_price(code):			# 삼성전자 코드 : 005930
    PATH = "uapi/domestic-stock/v1/quotations/inquire-price"
    URL = f"{URL_BASE}/{PATH}"
    headers = {"Content-Type":"application/json", 
            "authorization": f"Bearer {ACCESS_TOKEN}",          
#           OAuth 토큰이 필요한 API 경우 발급한 Access token
#           일반고객(Access token 유효기간 1일, OAuth 2.0의 Client Credentials Grant 절차를 준용)
#           법인(Access token 유효기간 3개월, Refresh token 유효기간 1년, OAuth 2.0의 Authorization Code Grant 절차를 준용)
            "appKey":APP_KEY,
            "appSecret":APP_SECRET,
            "tr_id":"FHKST01010100"}            # 거래 ID - FHKST01010100 : 주식 현재가
    # Query Parameter
    params = {                
    "fid_cond_mrkt_div_code":"J",               # FID 조건 시장 분류 코드 : J(주식, ETF, ETN)
    "fid_input_iscd":code,                      # FID 입력 종목코드 : 종목번호 6자리
    }
    res = requests.get(URL, headers=headers, params=params)
    return int(res.json()['output']['stck_prpr']) # 주식 현재가


def get_stock_balance():
    """주식 잔고조회"""
    PATH = "uapi/domestic-stock/v1/trading/inquire-balance"
    URL = f"{URL_BASE}/{PATH}"
    headers = {"Content-Type":"application/json", 
        "authorization":f"Bearer {ACCESS_TOKEN}",
        "appKey":APP_KEY,
        "appSecret":APP_SECRET,
        "tr_id":"VTTC8434R",
        "custtype":"P",
    }
    params = {
        "CANO": CANO,
        "ACNT_PRDT_CD": ACNT_PRDT_CD,
        "AFHR_FLPR_YN": "N",
        "OFL_YN": "",
        "INQR_DVSN": "02",
        "UNPR_DVSN": "01",
        "FUND_STTL_ICLD_YN": "N",
        "FNCG_AMT_AUTO_RDPT_YN": "N",
        "PRCS_DVSN": "01",
        "CTX_AREA_FK100": "",
        "CTX_AREA_NK100": ""
    }
    res = requests.get(URL, headers=headers, params=params)
    stock_list = res.json()['output1']
    evaluation = res.json()['output2']
    stock_dict = {}
    send_message(f"====주식 보유잔고====")
    for stock in stock_list:
        if int(stock['hldg_qty']) > 0: # 보유수량이 0보다 많으면
            stock_dict[stock['pdno']] = stock['hldg_qty'] # 상품번호가 key, 수량이 value
            send_message(f"{stock['prdt_name']}({stock['pdno']}): {stock['hldg_qty']}주")
            time.sleep(0.1)

    send_message(f"주식 평가 금액: {evaluation[0]['scts_evlu_amt']}원")
    time.sleep(0.1)
    send_message(f"평가 손익 합계: {evaluation[0]['evlu_pfls_smtl_amt']}원")
    time.sleep(0.1)
    send_message(f"총 평가 금액: {evaluation[0]['tot_evlu_amt']}원")
    time.sleep(0.1)
    send_message(f"=================")
    return stock_dict


# 보유 현금 조회
def get_balance():
    '''현금 잔고 조회'''
    PATH = "uapi/domestic-stock/v1/trading/inquire-psbl-order"
    URL = f"{URL_BASE}/{PATH}"
    headers = {"Content-Type":"application/json", 
        "authorization":f"Bearer {ACCESS_TOKEN}",
        "appKey":APP_KEY,
        "appSecret":APP_SECRET,
        "tr_id":"VTTC8908R",        # [실전투자] TTTC8908R [모의투자] VTTC8908R : 주식 잔고 조회
        "custtype":"P",             # 고객타입 : 개인
    }
    params = {
        "CANO": CANO,                   # 계좌 앞 8자리
        "ACNT_PRDT_CD": ACNT_PRDT_CD,   # 계좌 뒤 2자리
        "PDNO": "005930",               # 상품번호 (현재는 삼성전자)
        "ORD_UNPR": "00054500",         # 주문단가
        "ORD_DVSN": "00",               # 주문구분
        "CMA_EVLU_AMT_ICLD_YN": "N",    # CMA평가금액 포함여부
        "OVRS_ICLD_YN": "N",            # 해외포함여부
    }
    res = requests.get(URL, headers=headers, params=params)
    # print(res.json())
    balance = (int)(res.json()['output']['ord_psbl_cash'])
    send_message(f"주문 가능 현금 잔고: {balance}원")
    return int(balance)


def buy(code, qty):
    """주식 시장가 매수"""  
    PATH = "uapi/domestic-stock/v1/trading/order-cash"
    URL = f"{URL_BASE}/{PATH}"
    data = {
        "CANO": CANO,
        "ACNT_PRDT_CD": ACNT_PRDT_CD,
        "PDNO": code,
        "ORD_DVSN": "01",
        "ORD_QTY": str(int(qty)),
        "ORD_UNPR": "0",
    }
    headers = {"Content-Type":"application/json", 
        "authorization":f"Bearer {ACCESS_TOKEN}",
        "appKey":APP_KEY,
        "appSecret":APP_SECRET,
        "tr_id":"VTTC0802U",
        "custtype":"P",
        "hashkey" : hashkey(data)
    }
    res = requests.post(URL, headers=headers, data=json.dumps(data))
    if res.json()['rt_cd'] == '0':
        send_message(f"[매수 성공]{str(res.json())}")
        return True
    else:
        send_message(f"[매수 실패]{str(res.json())}")
        return False

def sell(code, qty):
    """주식 시장가 매도"""
    PATH = "uapi/domestic-stock/v1/trading/order-cash"
    URL = f"{URL_BASE}/{PATH}"
    data = {
        "CANO": CANO,
        "ACNT_PRDT_CD": ACNT_PRDT_CD,
        "PDNO": code,
        "ORD_DVSN": "07",
        "ORD_QTY": qty,
        "ORD_UNPR": "0",
    }
    headers = {"Content-Type":"application/json", 
        "authorization":f"Bearer {ACCESS_TOKEN}",
        "appKey":APP_KEY,
        "appSecret":APP_SECRET,
        "tr_id":"VTTC0801U",
        "custtype":"P",
        "hashkey" : hashkey(data)
    }
    res = requests.post(URL, headers=headers, data=json.dumps(data))
    if res.json()['rt_cd'] == '0':
        send_message(f"[매도 성공]{str(res.json())}")
        return True
    else:
        send_message(f"[매도 실패]{str(res.json())}")
        return False



def inquire_daily_order(code):
    """db mod_trs 업데이트를 위해 값들을 api에서 조회하여 tuple형식으로 반환해주는 함수"""
    PATH = "/uapi/domestic-stock/v1/trading/inquire-daily-ccld"
    URL = f"{URL_BASE}/{PATH}"
    headers = {"Content-Type":"application/json", 
        "authorization":f"Bearer {ACCESS_TOKEN}",
        "appKey":APP_KEY,
        "appSecret":APP_SECRET,
        "tr_id":"VTTC8001R",
        "custtype":"P",
    }

    now = datetime.datetime.today().strftime('%Y%m%d')
    
    params = {
        "CANO": CANO,
        "ACNT_PRDT_CD": ACNT_PRDT_CD,
        "INQR_STRT_DT": now, # 조회시작일자
        "INQR_END_DT": now, # 조회종료일자
        "SLL_BUY_DVSN_CD": "00", # 매도매수구분코드
        "INQR_DVSN": "01", # 정순
        "PDNO": code,
        "CCLD_DVSN": "00", # 체결구분 - 전체
        "ORD_GNO_BRNO": "", #주문채번지점번호 - null
        "ODNO": "", # 주문번호 : 주문시 한국투자증권 시스템에서 채번된 주문번호
        "INQR_DVSN_3": "00",
        "INQR_DVSN_1":"",
        "CTX_AREA_FK100":"",
        "CTX_AREA_NK100":""
    }
    res = requests.get(URL, headers=headers, params=params)
    result = res.json()['output1']
    
    mod_id = 2
    ord_dt = result['ord_dt']
    iem_cd = result['pdno']
    sby_dit_cd = result['sll_buy_dvsn_cd']
    cns_qty = result['tot_ccld_qty']
    orr_pr = result['tot_ccld_amt']

    return (mod_id, ord_dt, iem_cd, sby_dit_cd, cns_qty, orr_pr)



# DB 함수

In [ ]:
# db에서 기업리스트 가져오기
def get_company_list():
    conn =
    cur =

    query = "SELECT code FROM company_info "
    cur.execute(query)
    conn.commit()

    company_list=[]
    datas = cur.fetchall()

    for data in datas:
        company_list.append(data)

    return company_list


# 기업별 df뽑아서 상승세 check해서 기업select
def make_increase_company(company_list):
    conn = 
    cur = 

    for com in company_list:
        
        query = "SELECT * FROM mod_sign WHERE iem_cd={0}".format(com)
        cur.execute(query)
        conn.commit()

        company=[]
        datas = cur.fetchall()

        for data in datas:
            company.append(data)

        df = pd.DataFrame(company)

        df['aroondown'], df['aroonup'] = talib.AROON(df['high'], df['low'], timeperiod=14)
        com=df['code'][0]

        # up이 50보다 크고 down이 50보다 작음 : 상승세
        if (df['aroonup'][len(df)-1]> 50) & (df['aroondown'][len(df)-1] < 50):
            
            # 상승세 중에서도 100가까이 가고 30이하에 머물면 추세 발생 확률 높음
            if df['aroondown'][len(df)-1] <= 30:
                aroon_result[com] = df['aroonup'][len(df)-1]

    # value 값 작은순으로 정렬
    aroon_result = sorted(aroon_result.items(), key=lambda x: x[1], reverse=True)
    # aroon_result = sorted(aroon_result.items(), key=operator.itemgetter(1), )

    # 앞에서 5개만 선택
    aroon_result = aroon_result[:5]
    
    return aroon_result

In [ ]:
## 장 마감 후 업데이트 해줘야 할 tb : 
# 모델거래내역 mod_trs
# 모델자산내역 mod_act
    

# 오늘 주문한 종목코드 전부 조회해서 하나의 리스트로 만들어서 반환
def get_daily_order_list(code_list):
    daily_order_list = []
    for code in code_list:
        tuple = inquire_daily_order(code)
        daily_order_list.append(tuple)

    return daily_order_list

# 매매신호 db(tb mod_sign) insert
def insert_mod_sign(signal_list):
    cur = conn.cursor()
    
    sql = f"INSERT INTO mod_sign(mod_id, ord_sig, ord_sig_dt, iem_cd) " \
                "VALUES (" +','.join(["%s"]*4) + ");"
    cur.executemany(sql, signal_list)
    conn.commit()


# db(tb mod_trs) insert
def insert_mod_trs(list):
    cur = conn.cursor()
    
    sql = f"INSERT INTO mod_trs(mod_id, ord_dt, iem_cd, sby_dit_cd, cns_qty, orr_pr) " \
                "VALUES (" +','.join(["%s"]*6) + ");"
    cur.executemany(sql, list)
    conn.commit()

def insert_mod_act(list):
    cur = conn.cursor()
    
    sql = f"INSERT INTO mod_act(model, mod_ren_df, tot_mod_pri, tot_mod_prf, tot_mod_inv, tot_mod_rtr, tot_mod_iem_cd, tot_mod_mon_rtr, tot_mod_iem_rtr, tot_mod_iem_per_rtr, tot_mod_iem_qty) " \
                "VALUES (" +','.join(["%s"]*11) + ");"
    cur.executemany(sql, list)
    conn.commit()

# 모델원금 가져오는 함수 - 사용자가 돈 넣을 때마다 모델원금 업데이트해주기
# tb usr_trn_info(User자산내역)에 원금있으니까 id기준으로 중복제거조회 맨 마지막꺼 다 가져와서 합하기?


def inquire_model_balance(model, code_list):
    '''db mod_act에 들어갈 값들을 튜플로 반환해주는 함수'''
    PATH = "uapi/domestic-stock/v1/trading/inquire-balance"
    URL = f"{URL_BASE}/{PATH}"
    headers = {"Content-Type":"application/json", 
        "authorization":f"Bearer {ACCESS_TOKEN}",
        "appKey":APP_KEY,
        "appSecret":APP_SECRET,
        "tr_id":"VTTC8434R",
        "custtype":"P",
    }
    params = {
        "CANO": CANO,
        "ACNT_PRDT_CD": ACNT_PRDT_CD,
        "AFHR_FLPR_YN": "N",
        "OFL_YN": "",
        "INQR_DVSN": "02",
        "UNPR_DVSN": "01",
        "FUND_STTL_ICLD_YN": "N",
        "FNCG_AMT_AUTO_RDPT_YN": "N",
        "PRCS_DVSN": "01",
        "CTX_AREA_FK100": "",
        "CTX_AREA_NK100": ""
    }
    res = requests.get(URL, headers=headers, params=params)
    stock_list = res.json()['output1']
    evaluation = res.json()['output2']

    mod_ren_df = datetime.datetime.today() # 모델 업데이트 날짜
    tot_mod_pri =    
     #evaluation['dnca_tot_amt'] 
    # 모델원금 : api에서 (예수금총금액) 조회
    # 사용자가 돈 넣을 때마다 원금이 바뀌는데 그때 원금을 저장해두어서 가져와야하는거아닌가
    
    # 모델수익 = 평가자산-투자원금
    # tot_mod_prf = 0 # 모델수익
    tot_mod_inv = 0 #모델평가자산
    for stock in stock_list:
        if int(stock['hldg_qty']) > 0:
            tot_mod_inv += float(stock['evlu_amt'])
            # tot_mod_prf += float(stock['prpr']) - float(stock['pchs_amt']) # 모델수익 = 현재가-매입금액
    
    stock_dict = {}
    percent_dict = {}
    for stock in stock_list:
        if int(stock['hldg_qty']) > 0: # 보유수량이 0보다 많으면
            stock_dict[stock['pdno']] = stock['hldg_qty'] # 상품번호가 key, 수량이 value
            pchs_avg_pric = float(stock['pchs_avg_pric']) # 매입평균가격
            # 기업별 비중 구하기 : (기업별매입가*기업보유주식수)/평가금액
            percent = (pchs_avg_pric*int(stock['hldg_qty']))/tot_mod_inv
            percent_dict[stock['pdno']] = round(percent,3)

            time.sleep(0.1)

    tot_mod_rtr = evaluation[0]['asst_icdc_erng_rt'] # 수익률 (=평가손익율)
    tot_mod_iem_cd = code_list # 보유종목 리스트
    balance = get_balance()
    tot_mod_mon_rtr = balance/tot_mod_inv # 현금비중=(남은현금/평가금액)*100
    tot_mod_iem_rtr = (tot_mod_inv-balance)/tot_mod_inv #주식비중
    tot_mod_iem_per_rtr = percent_dict #기업별비중 딕셔너리 : 평가금액/(기업별매입가*기업보유주식수)
    tot_mod_iem_qty = stock_dict #기업별보유주식수 딕셔너리

    
    return (model, mod_ren_df, tot_mod_pri, tot_mod_prf, tot_mod_inv, tot_mod_rtr, tot_mod_iem_cd, tot_mod_mon_rtr, tot_mod_iem_rtr, tot_mod_iem_per_rtr, tot_mod_iem_qty)



# 머신러닝 모델 함수

In [ ]:

# 매매신호 생성코드 -> 보유기업 for문으로 돌면서 signal_list(tuple)에 생성된 신호 쌓기
def ML_make_signal(symbol_list):



    return signal_list


# n기간 라벨링 함수화
# 기업돌면서 list(tuple*5) 형식으로 뱉는 함수 하나 더 필요
def n_period_labeling(df):
    


    return 

# 후보코드

In [ ]:
# db관련
    

# # 마지막 매매신호 select
# def select_last_signal(code):
#     cur = conn.cursor()

#     query = "SELECT mod_id, ord_sig, ord_sig_dt, iem_cd FROM mod_sign WHERE mod_id='2' AND iem_cd={0} ORDER BY id DESC LIMIT 1".format(code)
#     # query = "SELECT * FROM mod_sign WHERE mod_id='2' AND iem_cd={0} ORDER BY id DESC LIMIT 1".format('003490')
#     cur.execute(query)
#     conn.commit()

#     company_list=[]
#     datas = cur.fetchall()
#     return datas[0]


# # 각 기업 조회해서 신호 리스트로 만들기
# def signal_tolist(symbol_list):
#     signal_list = []
#     for sym in symbol_list:
#         tuple = select_last_signal(sym)
#         signal_list.append(tuple)
#     return signal_list



# 모델원금 조회해오기
# def select_model_tot_price(model):
#     cur = conn.cursor()

#     query = "SELECT tot_mod_pri FROM mod_act WHERE mod_id={0} ORDER BY id DESC LIMIT 1".format(model)
#     cur.execute(query)
#     conn.commit()

#     company_list=[]
#     datas = cur.fetchall()
#     return datas[0][0]


# tb usr_trn_info에서 유저원금 조회
def select_user_tot_price():
    cur = conn.cursor()

    # 유저별로 맨 마지막값 하나만 조회하고 싶은데.....
    query = "SELECT distinct tot_cus_pri FROM usr_trn_info WHERE id (select max(id)) ORDER BY id DESC LIMIT 1".format(model)
    cur.execute(query)
    conn.commit()

    company_list=[]
    datas = cur.fetchall()
    return datas[0][0]

# 사용자 출금신호 코드

In [ ]:
# 유저 하고싶다고 하면 수익률안좋은기업팔기 
# -> for문으로 수익률 안좋은 기업부터 돌면서 팔고 금액 부족하면 다음 기업 판매(소수점내려서?)

1. tb usr_ofd_info(uSer입출금내역)을 계속 확인하면서 사용자출금신호가 들어오는지 확인
@ 입금출금신호(입금1, 출금2)
2. 신호가 출금이면 - 금액받아오고(ord_amt)
for문 수익률이 안좋은 기업 순으로 매도해서 출금요청금액 채우기
@ 여기서 기업마다 수익률 계산? 혹은 하루마다 늘 계산해두기?
@ 모델수익구하고 사용자지분으로 n빵하는게 사용자수익 (맞나)
3. db 업데이트


In [ ]:
# db trs_check에서 입출금입력여부 계속 확인
def check_withdraw():
    cur = conn.cursor()

    # userid별로 맨 마지막 값 조회
    query = "SELECT distinct tot_cus_pri FROM usr_trn_info WHERE id (select max(id)) ORDER BY id DESC LIMIT 1".format(model)
    cur.execute(query)
    conn.commit()

    company_list=[]
    datas = cur.fetchall()
    return datas[0][0]

# 자동매매 code

In [ ]:
def get_BSH_signal(signal_list):
    # 시그널 조사
    buy_signal_list=[]
    sell_signal_list=[]
    hold_signal_list=[]

    for datas in signal_list: # 전날 생성된 신호 조회
        signal = datas[1]
        code = datas[3]
        if signal == '1':
            buy_signal_list.append(code)
        elif signal=='-1':
            sell_signal_list.append(code)
        elif signal=='0':
            hold_signal_list.append(code)

    return buy_signal_list, sell_signal_list, hold_signal_list


In [ ]:
# 장 시간 끝나고 돌리는 try

# 딥러닝 - 17:05에 실행
def DL_calculation():
    model = '2'

    stock_dict = get_stock_balance() # 보유 주식 조회(딕셔너리)
    code_list = [code for code in stock_dict.keys()] # 보유 기업 조회

    # 장 마감 후 업데이트 해줘야 할 tb : 모델거래내역 mod_trs, 모델자산내역 mod_act 
    # 모델거래내역 mod_trs : 오늘 주문한 종목코드 전부 조회해서 하나의 리스트로 만들어서 반환
    daily_order_list = get_daily_order_list(code_list)
    insert_mod_trs(daily_order_list)
    # 모델자산내역 mod_act 
    model_tuple = inquire_model_balance(model, code_list)
    insert_mod_act(model_tuple)

    company_list = get_company_list() # db에서 기업 리스트 가져오기
    increase_list = make_increase_company(company_list) # 상승세인 기업 선정


    # 매매할 기업 업데이트
    max_com_count = 5
    if code_list != 5:
        additional_buy_count = max_com_count - len(code_list) # 추가로 매수할 종목 수
        
        for i in range(additional_buy_count):
            # 기업 같으면 pass
            if increase_list[i] in code_list:
                pass
            code_list.append(increase_list[i])

    
    # 매매신호 생성 함수(머신러닝,딥러닝) -> signal_list(tuple)
    signal_list = DL_make_signal(code_list)

    # 생성된 매매신호 db(tb mod_sign) 업데이트
    insert_mod_sign(signal_list)
    #생성된 맨 마지막 매매신호들 signal_list에 담겨있음
    
    # buy, sell, hold 시그널조사
    buy_signal_list, sell_signal_list, hold_signal_list = get_BSH_signal(signal_list)

    return buy_signal_list, sell_signal_list, hold_signal_list


In [ ]:
# 머신러닝 17:05에 실행
def ML_calculation():
    model = '1'

    stock_dict = get_stock_balance() # 보유 주식 조회(딕셔너리)
    code_list = [code for code in stock_dict.keys()] # 보유 기업 조회

    # 장 마감 후 업데이트 해줘야 할 tb : 모델거래내역 mod_trs, 모델자산내역 mod_act 
    # 모델거래내역 mod_trs : 오늘 주문한 종목코드 전부 조회해서 하나의 리스트로 만들어서 반환
    daily_order_list = get_daily_order_list(code_list)
    insert_mod_trs(daily_order_list)
    # 모델자산내역 mod_act 
    model_tuple = inquire_model_balance(model, code_list)
    insert_mod_act(model_tuple)

    company_list = get_company_list() # db에서 기업 리스트 가져오기
    increase_list = make_increase_company(company_list) # 상승세인 기업 선정


    # 매매할 기업 업데이트
    max_com_count = 5
    if code_list != 5:
        additional_buy_count = max_com_count - len(code_list) # 추가로 매수할 종목 수
        
        for i in range(additional_buy_count):
            # 기업 같으면 pass
            if increase_list[i] in code_list:
                pass
            code_list.append(increase_list[i])

    
    # 매매신호 생성 함수(머신러닝,딥러닝) -> signal_list(tuple)
    signal_list = ML_make_signal(code_list)

    # 생성된 매매신호 db(tb mod_sign) 업데이트
    insert_mod_sign(signal_list)
    #생성된 맨 마지막 매매신호들 signal_list에 담겨있음
    
    # buy, sell, hold 시그널조사
    buy_signal_list, sell_signal_list, hold_signal_list = get_BSH_signal(signal_list)

    return buy_signal_list, sell_signal_list, hold_signal_list


In [ ]:
# 자동매매 시작
from pandas.io.stata import relativedelta
import pause

try:
    ACCESS_TOKEN = get_access_token()

    send_message("===국내 주식 자동매매 프로그램을 시작합니다===")
    while True:
        t_now = datetime.datetime.now()
        t_9 = t_now.replace(hour=9, minute=0, second=0, microsecond=0)
        t_start = t_now.replace(hour=9, minute=5, second=0, microsecond=0)
        t_sell = t_now.replace(hour=15, minute=15, second=0, microsecond=0)
        t_exit = t_now.replace(hour=15, minute=20, second=0,microsecond=0)
        t_close_buy = t_now.replace(hour=15, minute=40, second=0, microsecond=0)
        t_close_buy_exit = t_now.replace(hour=15, minute=55, second=0, microsecond=0)

        today = datetime.date.today()
        next_monday = today + datetime.timedelta(days=-today.weekday(), weeks=1) # t_now 기준 그 다음 월요일 날짜
        today_day = today.weekday()
        # str으로 바꾸기
        next_monday = next_monday.strftime("%Y-%m-%d 0:0:0")
        # datetime.datetime 형식으로 바꾸기
        next_monday = datetime.datetime.strptime(next_monday, '%Y-%m-%d %H:%M:%S')

        t_calculate_start = t_now.replace(hour=17, minute=30, second=0, microsecond=0)
        t_calculate_end = t_calculate_start + relativedelta(hours = 15)


        # 토요일이나 일요일이면 그 다음 월요일 자정이 될 때까지 pause
        if today_day == 5 or today_day == 6:
            pause.until(next_monday)
            continue


        # 장외 시간 : PM 05:30 ~ AM 08:30 : 계산
        if t_calculate_start < t_now < t_calculate_end:
            stock_dict = get_stock_balance() # 보유 주식 조회(딕셔너리)
    
            total_cash = get_balance() # 보유 현금 조회
            total_cash -= total_cash*0.014
            
            buy_signal_list, sell_signal_list, hold_signal_list = DL_calculation()

            if len(buy_signal_list) != 0:
                target_buy_count = len(buy_signal_list) #매수할 종목 수
                buy_percent = round(1/target_buy_count, 3) # 종목당 매수 금액 비율
                buy_amount = total_cash * buy_percent  # 종목별 주문 금액 계산
            continue
        
        # 장 시간 : AM 09:05 ~ PM 03:20 : 매수
        if t_start < t_now < t_close_buy :

            # 보유주식없고 매수신호 없는 경우 
            if stock_dict == False and buy_signal_list==[]:
                
                # 15:40까지 잠시 멈추기
                now_time = datetime.datetime.now()
                now_time = now_time.strftime("%Y-%m-%d 15:40:0")
                now_time = datetime.datetime.strptime(now_time, '%Y-%m-%d %H:%M:%S')
                pause.until(now_time)

            else:
                # 잔고 부족하면 프로그램 종료
                current_cash = get_balance() #잔고조회
                if current_cash < current_price: 
                    continue
                
                for code in buy_signal_list:
                    current_price = get_current_price(code) # 해당 주식 현재가 조회
                    buy_qty = 0  # 매수할 수량 초기화
                    buy_qty = int(buy_amount // current_price)
                    result = buy(code, buy_qty)
                    time.sleep(1)

                    
                    # 잔고, 보유수량 업데이트할 필요 없음 - api로 조회
            continue

        # PM 03:40 ~ PM 3:55 : 신호 매도면 종가가격으로 매도
        if t_close_buy < t_now < t_close_buy_exit:
            for code in sell_signal_list:
                qty = stock_dict[code] # 보유 주식 수
                result = sell(code, qty)
                # sell하면 리스트에서 기업 삭제해야하나? api자동업데이트니까 안해도되겠지..?

                time.sleep(1)
            continue

        if t_close_buy_exit < t_now:  # PM 03:55 ~ :다시 while문 처음부터 시작
            continue

except Exception as e:
    send_message(f"[오류 발생]{e}")
    time.sleep(1)


# code test

In [ ]:
import datetime
today = datetime.date.today()
next_monday = today + datetime.timedelta(days=-today.weekday(), weeks=1)
today_day = today.weekday()
next_monday = next_monday.strftime("%Y-%m-%d 0:0:0")
date_time_obj = datetime.datetime.strptime(next_monday, '%Y-%m-%d %H:%M:%S')
import pause

pause.until(date_time_obj)

In [ ]:
import datetime
import pause
test=5
test2=10
test3 = 15

if test==5:
    if test2==10:
        now_time = datetime.datetime.now()
        now_time = now_time.strftime("%Y-%m-%d 09:04:0")
        now_time = datetime.datetime.strptime(now_time, '%Y-%m-%d %H:%M:%S')
        pause.until(now_time)
    else:
        test=4

if test3==15:
    print('성공')

In [ ]:
# 딥러닝 시그널 함수
model = '2'
stock_dict = get_stock_balance() # 보유 주식 조회(딕셔너리)
print('1')
symbol_list = [sym for sym in stock_dict.keys()] #보유 주식 조회 후에 기업 확인
print('2')
# company_list = get_company_list() # db에서 기업 리스트 가져오기
print('3')
increase_company = ['000540', '004890', '006740', '008770', '017370']# 상승세인 기업 선정 - make_increase_company()
# 보유 기업 조회해서 symbol_list에 추가
max_com_count = 5
if symbol_list != 5:
    additional_buy_count = max_com_count - len(symbol_list) # 추가로 매수할 종목 수
    for i in range(additional_buy_count):
        # 기업 같으면 pass
        if increase_company[i] in symbol_list:
            pass
        symbol_list.append(increase_company[i])
        print('4')

# 딥러닝 시그널 생성
signal_list = []
for sym in symbol_list:
    result = deep_learning_model(sym)
    signal_list.append(DL_make_signal(result))
    print(signal_list)
    print('5')
# 시그널 db 업데이트
insert_mod_sign(signal_list)
print('6')
# 시그널 조사
buy_signal_list, sell_signal_list, hold_signal_list = get_BSH_signal(signal_list)

In [7]:
try:
    while True:
        print('while문 처음')
        test = 5
        test2 = 10
        test3 = 15
        if test == 5:
            print('if1')
            if test2 == 9:
                print('if2')
            else:
                if test3 == 15:
                    print('if3')
                    continue
                for i in range(1):
                    print(i)
                    
            continue
        print('while문 끝')
except Exception as e:
    print('오류')  

while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음
if1
if3
while문 처음


KeyboardInterrupt: 